In [1]:
import os
import glob
import time
from datetime import timedelta, datetime
import numpy as np
import pandas as pd
import qgrid

from plotly.graph_objs import Scatter,Layout
import plotly
import plotly.offline as py
import plotly.graph_objs as go
from plotly.subplots import make_subplots

#setting offilne
plotly.offline.init_notebook_mode(connected=True)
import gezi

from projects.feed.rank.monitor.taurus import Taurus

In [2]:
%%html
<style>
.output_wrapper, .output {
    height:auto !important;
    max-height:10000px;  /* your desired max-height here */
}
.output_scroll {
    box-shadow:none !important;
    webkit-box-shadow:none !important;
}
</style>

In [3]:
last_days = 30
start_time = None
end_time = None
# start_time = 20191210
# end_time = 20191220
# abids = [8,15,16]
# abids = [16, 8]
# abids = [16]
# abids = [8, 15]
# abids = [15]
abids = [17]
# abids = [17]
# abids = [9]

assert len(abids) < 2, 'FIXME only 1 abid is ok now, as natural_diff wrong currenlty TODO'
product = 'sgsapp'
# product = 'newmse'

diff_spans_ = {
    8: [20200313, 20200319],
#     12: [20190130, 20200205],
#     11: [20190130, 20200205],
    9: [20200325, 20200331],
    10: [20200325, 20200331],
    11: [20200325, 20200331],
    15: [20200325, 20200331],
    16: [20200325, 20200331],
    17: [20200325, 20200331],
}
diff_spans = {}
for abid in abids:
  diff_spans[abid] = diff_spans_[abid]

diff_spans = None

In [4]:
worker_daily = Taurus()
worker_daily.init(abids, last_days, 'daily', product=product,
                  diff_spans=diff_spans, start_time=start_time, end_time=end_time)
worker_daily.run()

# for name 1(tuwen,video,small_video,total) 2(quality,total) 3(recommend,relative,total)
def show_daily(name, use_diff=True, quality=False, field=None):
  worker_daily.show(name, quality, field, use_diff=False)

SELECT * FROM feed_abtest_video_type_common_daily 
                WHERE product = 'sgsapp'
                AND abtest in ('17','5','4','6') 
                AND date BETWEEN '20200618' AND '20200719'
                AND video_type in ('0', '1', '2', 'total')
          
/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

/home/gezi/mine/pikachu/projects/feed/rank/monitor/taurus.py:169: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.

16.219170093536377


In [5]:
w = worker_daily
d = worker_daily.ratio2
d = d.sort_values('date', ascending=False)
# pd.set_option('precision', 5)  
names = ['dis_user', 'click_user', 'click', 'duration', 'refresh_times', 'read_files', 'ctr', 'read_ratio', 'dur1', 'dur2', 
         'doc_dur', 'finish_ratio', 'praise', 'favor', 'share']
# d2 = d[d.name!='small_video'].groupby(['name', 'data_obj', 'abtest']).head(6).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]
d2 = d.groupby(['name', 'data_obj', 'abtest']).head(1).groupby(['name', 'data_obj', 'abtest'], as_index=False).mean()[['name', 'abtest', 'data_obj', *names]]

# qgrid.show_grid(d2)
# d.groupby(['name', 'data_obj', 'abtest']).head(1)

In [6]:
d_ = d2[d2.data_obj=='total_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [7]:
d_ = d2[d2.data_obj=='quality_total']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [8]:
d_ = d2[d2.data_obj=='total_relative']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [9]:
d_ = d2[d2.data_obj=='total_recommend']
for abid in abids:
    fig = go.Figure(data=[
        go.Bar(name=name, 
               x=d_[d_.abtest==abid].name, 
               y=d_[d_.abtest==abid][name]) for name in names]
        )
    # Change the bar mode
    fig.update_layout(barmode='group', title_text='abtest:%d' % abid)
    fig.show()

In [10]:
w.ratio2[w.ratio2.name=='video'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
740  20200718  0.003639    0.021892  0.036037  0.064336       0.018807   
716  20200717  0.001606    0.026858  0.052828  0.049810       0.022006   
692  20200716  0.000469    0.022367  0.050363  0.028140       0.007000   
668  20200715 -0.000324    0.040275  0.056267  0.036269       0.044326   
644  20200714 -0.004182    0.037513  0.027261  0.034648       0.006646   
620  20200713  0.001589    0.036027  0.038877  0.045461       0.011735   
596  20200712 -0.001682    0.036515  0.059536  0.063258       0.002545   
572  20200711  0.003005    0.027717  0.030270  0.027012      -0.001070   
548  20200710 -0.000784    0.027722  0.048830  0.044925       0.002651   
524  20200709  0.000487    0.021414  0.032034  0.034217       0.005426   
500  20200708 -0.001991    0.021066  0.025371  0.024819       0.014910   
476  20200707  0.003141    0.017162  0.025525  0.008845       0.002339   
452  20200706  0.005329    0.018177  0.026499  0.011396      -0.002907   
428  20200705  0.006792    0.017485  0.008829  0.010380       0.005168   
404  20200704  0.007092    0.008289 -0.002733 -0.001322      -0.016271   
380  20200703  0.002660    0.016304  0.011913  0.004500       0.002980   
356  20200702  0.008474    0.013751  0.036068  0.043933       0.022384   
332  20200701  0.007127    0.011920  0.026030  0.014695       0.019461   
308  20200630  0.005556    0.017702  0.041334  0.044736       0.004389   
284  20200629  0.005685    0.013984  0.006819  0.004462       0.007744   
260  20200628  0.003604    0.016890 -0.011645 -0.017042      -0.010991   
236  20200627  0.005585   -0.000415 -0.020417 -0.004585       0.006500   
212  20200626  0.006070    0.011635  0.004873  0.002165       0.017378   
188  20200625  0.006850    0.012203 -0.006277  0.000870       0.003260   
164  20200624  0.003648    0.018375  0.019449  0.010024       0.010708   
140  20200623  0.001972    0.006841  0.012100  0.013473       0.031299   
116  20200622 -0.004662   -0.027125 -0.033774 -0.026699       0.005294   
92   20200621 -0.007859   -0.035214 -0.078313 -0.073064       0.030645   
68   20200620 -0.003801   -0.043166 -0.085088 -0.073802       0.009011   
44   20200619 -0.004907    0.004170 -0.003885  0.002323       0.065121   
20   20200618 -0.006080    0.103657  0.124587  0.112458       0.198519   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
740    0.032342  0.013391    0.018154  0.060523  0.041540  0.027230   
716    0.051168  0.023105    0.025193  0.048164  0.022353 -0.002935   
692    0.049875  0.024166    0.021890  0.027657  0.005625 -0.021184   
668    0.056574  0.020712    0.040550  0.036523 -0.003854 -0.018962   
644    0.031641  0.006233    0.041829  0.039022 -0.002726  0.007122   
620    0.037240  0.023687    0.034373  0.043822  0.009133  0.006383   
596    0.061312  0.035389    0.038235  0.065023  0.025771  0.003505   
572    0.027188  0.011235    0.024644  0.023942 -0.000680 -0.003156   
548    0.049635  0.029847    0.028506  0.045726  0.016662 -0.003718   
524    0.031544  0.020908    0.020917  0.033725  0.012557  0.002107   
500    0.027420  0.029327    0.023076  0.026873  0.003630 -0.000579   
476    0.022344  0.019705    0.014002  0.005717 -0.008164 -0.016271   
452    0.021041  0.013281    0.012780  0.006019 -0.006748 -0.014718   
428    0.002047 -0.000163    0.010623  0.003578 -0.006969  0.001515   
404   -0.009759 -0.016795    0.001183 -0.008350 -0.009497  0.001078   
380    0.009241 -0.005570    0.013613  0.001832 -0.011602 -0.007439   
356    0.027411  0.006013    0.005230  0.035172  0.029739  0.007467   
332    0.018780  0.009411    0.004761  0.007498  0.002724 -0.011148   
308    0.035577  0.029141    0.012035  0.038959  0.026559  0.003208   
284    0.001131  0.000606    0.008261 -0.001232 -0.009431 -0.002401   
260   -0.015179 -0.014393    0.013242 -0.020568 -0.033370 -0.005499   
236   -0.025878 -0.028897   -0.005964 -0.010111 -0.004120  0.016031   
212   -

In [11]:
w.ratio2[w.ratio2.name=='total'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
728  20200718  0.004576    0.010021  0.030798  0.049723       0.018461   
704  20200717  0.002025    0.014048  0.043479  0.037617       0.025409   
680  20200716  0.001612    0.015100  0.042147  0.025891       0.021255   
656  20200715 -0.001207    0.006852  0.053295  0.015170       0.020901   
632  20200714 -0.003661    0.005836  0.025837  0.022461       0.016340   
608  20200713  0.002055    0.021471  0.028913  0.026265       0.006378   
584  20200712 -0.001636    0.012187  0.046851  0.039113       0.014977   
560  20200711  0.003817    0.011698  0.028485  0.020807       0.012375   
536  20200710 -0.000689    0.007147  0.043674  0.033970       0.008992   
512  20200709  0.000524    0.001450  0.028814  0.026083       0.002627   
488  20200708 -0.001582   -0.003790  0.017713  0.009930      -0.005380   
464  20200707  0.003500    0.009323  0.022746  0.010953       0.009931   
440  20200706  0.006139    0.010857  0.026041  0.018586       0.016773   
416  20200705  0.007157    0.011318  0.009652  0.007698       0.018592   
392  20200704  0.006918    0.006317  0.004461  0.010336       0.011397   
368  20200703  0.003033    0.007418  0.013540  0.012557       0.023261   
344  20200702  0.009530    0.009605  0.032837  0.037596       0.033376   
320  20200701  0.007204    0.012101  0.019192  0.015345       0.018602   
296  20200630  0.006636    0.011682  0.029356  0.031256       0.015935   
272  20200629  0.005192    0.004440  0.004978  0.008612       0.013189   
248  20200628  0.002988    0.006186 -0.008290 -0.000677       0.007424   
224  20200627  0.006973    0.001854 -0.012398  0.007731       0.003908   
200  20200626  0.005910    0.008303  0.005059  0.013902       0.022838   
176  20200625  0.006714    0.010705 -0.003691  0.005142       0.003700   
152  20200624  0.003821    0.013907  0.016124  0.013650       0.017641   
128  20200623  0.002453    0.003886  0.008982  0.012842       0.021132   
104  20200622 -0.004728   -0.015842 -0.026835 -0.017061       0.005922   
80   20200621 -0.007054   -0.024438 -0.055111 -0.038689       0.006020   
56   20200620 -0.003638   -0.021654 -0.064298 -0.042745       0.003903   
32   20200619 -0.004384   -0.014219 -0.003726 -0.001944       0.006051   
8    20200618 -0.006343    0.015499  0.078222  0.047917      -0.011277   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
728    0.026137  0.009672    0.005423  0.044941  0.039297  0.018275   
704    0.041397  0.016153    0.012012  0.035542  0.023264 -0.005680   
680    0.040476  0.018760    0.013471  0.024242  0.010625 -0.015625   
656    0.054534  0.013215    0.008111  0.016300  0.008023 -0.036229   
632    0.029639 -0.002567    0.009611  0.026199  0.016328 -0.003365   
608    0.026811  0.008822    0.019377  0.024169  0.004679 -0.002555   
584    0.048560  0.013605    0.013857  0.040800  0.026540 -0.007395   
560    0.024583 -0.000227    0.007848  0.016927  0.009005 -0.007477   
536    0.044377  0.015714    0.007862  0.034662  0.026513 -0.009295   
512    0.028285  0.009620    0.000932  0.025548  0.024591 -0.002668   
488    0.019332  0.013164   -0.002192  0.011540  0.013739 -0.007655   
464    0.019191  0.007327    0.005794  0.007438  0.001627 -0.011535   
440    0.019767  0.003915    0.004694  0.012356  0.007596 -0.007270   
416    0.002494 -0.005828    0.004136  0.000541 -0.003582 -0.001958   
392   -0.002434 -0.009423   -0.000595  0.003406  0.004028  0.005630   
368    0.010481 -0.008797    0.004374  0.009491  0.005105 -0.001040   
344    0.023124  0.001276    0.000081  0.027802  0.027717  0.004511   
320    0.011908  0.002233    0.004875  0.008073  0.003146 -0.003817   
296    0.022551  0.015029    0.005004  0.024448  0.019323  0.001821   
272   -0.000214 -0.004357   -0.000734  0.003387  0.004099  0.003590   
248   -0.011232 -0.015674    0.003198 -0.003646 -0.006836  0.007657   
224   -0.019259 -0.020413   -0.005081  0.000747  0.005857  0.020314   
200   -

In [12]:
w.ratio2[w.ratio2.name=='tuwen'][w.ratio2.data_obj=='quality_total'][['date', *names]].sort_values('date', ascending=False)

/home/gezi/env/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: UserWarning:

Boolean Series key will be reindexed to match DataFrame index.



date  dis_user  click_user     click  duration  refresh_times  \
734  20200718  0.004031    0.002140  0.011252  0.020941       0.018495   
710  20200717  0.001919    0.004548  0.009188  0.013829       0.026983   
686  20200716  0.001300    0.007495  0.014375  0.021351       0.027162   
662  20200715 -0.001313   -0.007543  0.021946 -0.030042       0.009443   
638  20200714 -0.004104   -0.004415  0.010461 -0.002416       0.021259   
614  20200713  0.002293    0.015436 -0.009942 -0.010593       0.004101   
590  20200712 -0.002039    0.003151 -0.005463 -0.009779       0.021258   
566  20200711  0.003522    0.002887  0.009505  0.006518       0.018423   
542  20200710 -0.000717   -0.002677  0.011841  0.012295       0.011759   
518  20200709  0.000416   -0.004796  0.005458  0.009991       0.001653   
494  20200708 -0.001213   -0.011946 -0.018986 -0.017980      -0.014173   
470  20200707  0.003229    0.000222  0.003500  0.013419       0.012852   
446  20200706  0.006670    0.004603  0.023270  0.030026       0.025655   
422  20200705  0.006475    0.001451  0.004046  0.001444       0.025060   
398  20200704  0.007184    0.000811  0.022899  0.031225       0.024112   
374  20200703  0.002524    0.003778  0.017526  0.025909       0.033429   
350  20200702  0.008843    0.004381  0.024178  0.027765       0.038749   
326  20200701  0.007335    0.007764  0.003434  0.017243       0.018412   
302  20200630  0.006652    0.005316 -0.004345  0.009384       0.021037   
278  20200629  0.004463   -0.005461 -0.001182  0.015995       0.015853   
254  20200628  0.002662    0.000173  0.004751  0.026452       0.015927   
230  20200627  0.005122   -0.004311  0.007361  0.028901       0.002320   
206  20200626  0.004585    0.006007  0.007427  0.037558       0.025722   
182  20200625  0.005567    0.003957 -0.000287  0.012526       0.003989   
158  20200624  0.003305    0.001894  0.006215  0.019964       0.020962   
134  20200623  0.002159   -0.002396  0.000279  0.012081       0.016409   
110  20200622 -0.004573   -0.014782 -0.010510 -0.002938       0.006766   
86   20200621 -0.007784   -0.027024  0.005593  0.018303      -0.005270   
62   20200620 -0.003928   -0.019905 -0.004029  0.006766       0.001962   
38   20200619 -0.004861   -0.021618 -0.004326 -0.009098      -0.022969   
14   20200618 -0.006456   -0.032739 -0.053995 -0.059516      -0.121748   

     read_files       ctr  read_ratio      dur1      dur2   doc_dur  \
734    0.007128 -0.009243   -0.001875  0.016760  0.018629  0.009556   
710    0.007270 -0.014916    0.002650  0.011885  0.009169  0.004575   
686    0.013070 -0.007001    0.006187  0.020036  0.013761  0.006861   
662    0.023229  0.009223   -0.006160 -0.028887 -0.023110 -0.050879   
638    0.014551 -0.000376   -0.000217  0.001598  0.001566 -0.012746   
614   -0.012207 -0.009872    0.013120 -0.012859 -0.025656 -0.000705   
590   -0.003426 -0.016622    0.005212 -0.007745 -0.012930 -0.004358   
566    0.005984 -0.001320   -0.000635  0.002980  0.003628 -0.003123   
542    0.012546  0.004880   -0.001935  0.012994  0.014854  0.000411   
518    0.005042  0.007510   -0.005202  0.009557  0.014809  0.004501   
494   -0.017795 -0.006603   -0.010709 -0.016781 -0.006226  0.000994   
470    0.000229 -0.007250   -0.003012  0.010134  0.013191  0.009844   
446    0.016482 -0.003747   -0.002046  0.023190  0.025239  0.006538   
422   -0.002424 -0.017814   -0.004988 -0.005012 -0.000044 -0.002632   
398    0.015631  0.009533   -0.006324  0.023887  0.030429  0.008066   
374    0.014965 -0.008586    0.001256  0.023323  0.022006  0.008201   
350    0.015204 -0.007996   -0.004418  0.018740  0.023256  0.003473   
326   -0.003853 -0.011910    0.000451  0.009847  0.009332  0.013726   
302   -0.010934 -0.018481   -0.001329  0.002720  0.004035  0.013775   
278   -0.005632 -0.012799   -0.009862  0.011470  0.021514  0.017170   
254    0.002104 -0.003613   -0.002472  0.023745  0.026282  0.021575   
230    0.002225  0.001415   -0.009381  0.023654  0.033317  0.021388   
206    

In [13]:
show_daily('total_quality_total')

In [14]:
show_daily('total_quality_total')

In [15]:
show_daily('tuwen_quality_total')

In [16]:
show_daily('video_total_total')

In [17]:
show_daily('video_total_recommend')

In [18]:
show_daily('video_total_relative')

refresh_times with same vals ignore


In [19]:
show_daily('tuwen_total_total')

In [20]:
w.ratio

product_name      date         name           data_obj  abtest        id  \
0         sgsapp  20200618  small_video  quality_recommend      17 -0.000002   
1         sgsapp  20200618  small_video   quality_relative      17 -0.000002   
2         sgsapp  20200618  small_video      quality_total      17 -0.000002   
3         sgsapp  20200618  small_video    total_recommend      17 -0.000002   
4         sgsapp  20200618  small_video     total_relative      17 -0.000002   
..           ...       ...          ...                ...     ...       ...   
739       sgsapp  20200718        video   quality_relative      17 -0.000002   
740       sgsapp  20200718        video      quality_total      17 -0.000002   
741       sgsapp  20200718        video    total_recommend      17 -0.000002   
742       sgsapp  20200718        video     total_relative      17 -0.000002   
743       sgsapp  20200718        video        total_total      17 -0.000002   

          dis  dis_user  refresh_times  real_dis  ...       ctr  real_ctr  \
0   -0.018601  0.025156      -0.479339 -0.025543  ... -0.028244 -0.034499   
1   -0.354365  0.015184       0.000000  0.000000  ... -0.122598 -0.441953   
2   -0.032339  0.022356      -0.091501 -0.025410  ... -0.397590 -0.417086   
3   -0.019973  0.024940      -0.369620 -0.023651  ... -0.022973 -0.021285   
4   -0.229325  0.025780       0.000000  0.000000  ... -0.143570 -0.342458   
..        ...       ...            ...       ...  ...       ...       ...   
739  0.019508  0.017155       0.000000  0.000000  ...  0.013439  0.033190   
740  0.022341  0.003639       0.018807  0.018611  ...  0.013391  0.017103   
741  0.020741 -0.006733       0.041286  0.021421  ...  0.021493  0.020808   
742  0.022723  0.007894       0.000000  0.167617  ...  0.007801 -0.174541   
743  0.019270 -0.006457       0.035466  0.018849  ...  0.014902  0.015324   

     read_ratio      dur1      dur2  finish_ratio  read_files   doc_dur  \
0     -0.108354 -0.091525  0.016433      0.052163   -0.064574 -0.027952   
1     -0.097020 -0.362040 -0.304594      0.361648   -0.452003  0.155940   
2     -0.108516 -0.347990 -0.271628      0.308842   -0.424780  0.127016   
3      0.007060 -0.062927 -0.070316     -0.071911   -0.064457  0.000891   
4     -0.067982 -0.303289 -0.259598      0.175523   -0.361405  0.090467   
..          ...       ...       ...           ...         ...       ...   
739    0.004145  0.047689  0.043359      0.022668    0.015786  0.031294   
740    0.018154  0.060523  0.041540      0.033565    0.032342  0.027230   
741    0.015947  0.041852  0.025437      0.021209    0.049706 -0.007502   
742    0.016626  0.048327  0.031179      0.024979    0.022626  0.024986   
743    0.023082  0.057632  0.033726      0.035368    0.041212  0.015700   

      refresh  refresh2  
0   -0.490441 -0.435764  
1   -0.015570  0.087661  
2   -0.111306 -0.003412  
3   -0.384120 -0.384759  
4   -0.025571  0.042345  
..        ...       ...  
739 -0.016868 -0.020927  
740  0.015105 -0.003022  
741  0.048270  0.031806  
742 -0.007874 -0.024096  
743  0.042131  0.018632  

[744 rows x 33 columns]